In [3]:
# Library imports

import pandas as pd
import os
from qualitative_analysis import (
    clean_and_normalize,
    load_data,
    sanitize_dataframe
)
from qualitative_analysis.scenario_runner import run_scenarios
from qualitative_analysis.evaluation import (
    compute_kappa_metrics,
    run_alt_test_on_results,
    compute_classification_metrics_from_results
)

c:\Users\ocler\miniconda3\envs\gpt_rl\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [ ]:
# Data loading

# Define data directory
data_dir = 'data/multiclass_user_case'
os.makedirs(data_dir, exist_ok=True)

# Define the path to your dataset
data_file_path = os.path.join(data_dir, 'llm_generation.xlsx')

# Load the data
data = load_data(data_file_path, file_type='xlsx', delimiter=';')

# Preview the data
data.head()

Code        model   prompt  \
0     1  GPT-4o mini  correct   
1     1  GPT-4o mini  correct   
2     1  GPT-4o mini  correct   
3     1  GPT-4o mini  correct   
4     1  GPT-4o mini  correct   

                                                 but  \
0  Ton but est de trouver la pièce qui aide ces d...   
1  Ton but est de trouver la pièce qui aide ces d...   
2  Ton but est de trouver la pièce qui aide ces d...   
3  Ton but est de trouver la pièce qui aide ces d...   
4  Ton but est de trouver la pièce qui aide ces d...   

                                    réponse_attendue  \
0  Le composant reliant les capteurs avec les act...   
1  Le composant reliant les capteurs avec les act...   
2  Le composant reliant les capteurs avec les act...   
3  Le composant reliant les capteurs avec les act...   
4  Le composant reliant les capteurs avec les act...   

                                         réponse_llm  iteration  Rater_Oli  \
0  La partie d'un robot qui relie les capteurs et...          1        2.0   
1  La partie d'un robot qui relie les capteurs et...          2        NaN   
2  La partie d'un robot qui relie les capteurs et...          3        NaN   
3  La partie d'un robot qui relie les capteurs et...          4        NaN   
4  La partie d'un robot qui relie les capteurs et...          5        NaN   

   Invalid_Oli  Rater_chloe  Invalid_chloe  Rater_RA  Invalid_RA  
0        False          2.0          False       1.0       False  
1        False          NaN          False       NaN       False  
2        False          NaN          False       NaN       False  
3        False          NaN          False       NaN       False  
4        False          NaN          False       NaN       False

In [ ]:
# 1) Now define the new column names for cleaning
text_columns = ["réponse_attendue", "réponse_llm"]
integer_columns = ["Code", "iteration", "Rater_Oli", "Rater_chloe", "Rater_RA"]

# 2) Clean and normalize the new columns
for col in text_columns:
    data[col] = clean_and_normalize(data[col])

# 4) Convert selected columns to integers, preserving NaNs
for col in integer_columns:
    data[col] = pd.to_numeric(data[col], errors="coerce").astype("Int64")  # Uses nullable integer type

# 5) Sanitize the DataFrame
data = sanitize_dataframe(data)

In [4]:
# Combine texts and entries

data['verbatim'] = data.apply(
    lambda row: (
        f"réponse_attendue: {row['réponse_attendue']}\n\n"
        f"réponse_llm: {row['réponse_llm']}\n\n"
    ),
    axis=1
)

# Extract the list of verbatims
verbatims = data['verbatim'].tolist()

print(f"Total number of verbatims: {len(verbatims)}")
print(f"Verbatim example:\n{verbatims[0]}")

Total number of verbatims: 720
Verbatim example:
réponse_attendue: Le composant reliant les capteurs avec les actionneurs est la carte de controle ou le microcontroleur.

réponse_llm: La partie d'un robot qui relie les capteurs et les moteurs pour aider a eviter les obstacles est generalement appelee le **systeme de controle** ou **unite de controle**. Ce systeme peut inclure un microcontroleur ou un ordinateur embarque qui recoit les donnees des capteurs (comme des capteurs de distance, des cameras, ou des capteurs infrarouges) et utilise ces informations pour prendre des decisions. Ensuite, il envoie des commandes aux moteurs pour ajuster la direction ou la vitesse du robot afin d'eviter les obstacles. Ce processus fait souvent partie d'un algorithme de navigation ou de traitement de signal qui permet au robot de reagir en temps reel a son environnement.




In [7]:
scenarios = [
    {
        "provider_llm1": "azure",
        "model_name_llm1": "gpt-4o",
        "temperature_llm1": 0,

        # For the "improver" LLM2
        "provider_llm2": "azure",
        "model_name_llm2": "gpt-4o",
        "temperature_llm2": 0.7,

        "max_iterations": 1,
        "n_completions": 1,
        "prompt_name": "French",
        
        # Data configuration
        "subsample_size": -1,  # Size of data subset to use
        "use_validation_set": False,  # Whether to use a validation set
        "validation_size": 10,  # Size of validation set (if used)
        "random_state": 42,  # Random state for reproducibility

        # Our initial prompt
        "template": """
Vous êtes un assistant chargé d’évaluer des entrées de données.

Les données comprennent les colonnes suivantes :
- "réponse_attendue": Un passage de réponse considérée comme satisfaisante
- "réponse_llm": La réponse fournie par le LLM, à juger
- "iteration": Identifiant

Voici une entrée à évaluer :
{verbatim_text}

Tâche d’évaluation :
Évaluer si la réponse_llm répond adéquatement, c'est à dire qu'elle correspond à la réponse attendue, en utilisant l’échelle suivante :

0 : La réponse générée ne permet pas du tout de répondre à la question posée (hors sujet, incomplète ou incorrecte).
1 : La réponse générée permet difficilement de répondre à la question, car elle est vague, trop ou pas assez détaillée.
2 : La réponse générée permet de répondre clairement à la question.
""",
        "prefix": "Classification",
        "json_output": True,
        "selected_fields": ["Classification"],
        "label_type": "int",
        "response_template":
        """
Please follow the JSON format below:
```json
{{
  "Reasoning": "Your text here",
  "Classification": "Your integer here"
}}
""",
    },
        {
        "provider_llm1": "azure",
        "model_name_llm1": "gpt-4o",
        "temperature_llm1": 0,

        # For the "improver" LLM2
        "provider_llm2": "azure",
        "model_name_llm2": "gpt-4o",
        "temperature_llm2": 0.7,

        "max_iterations": 1,
        "n_completions": 1,
        "prompt_name": "English",
        
        # Data configuration
        "subsample_size": -1,  # Size of data subset to use
        "use_validation_set": False,  # Whether to use a validation set
        "validation_size": 10,  # Size of validation set (if used)
        "random_state": 42,  # Random state for reproducibility

        # Our initial prompt
        "template": """
You are an assistant that evaluates data entries.

The data has the following columns:
- "réponse_attendue":  An excerpt of a reference answer considered satisfactory
- "réponse_llm": The answer provided by the LLM, to be evaluated
- "iteration": Identifier

Here is an entry to evaluate:
{verbatim_text}

Evaluation Task:
Evaluate whether the réponse_llm adequately matches the réponse_attendue using the following scale:

0: The generated answer does not help at all to answer the question (off-topic, incomplete, or incorrect).
1: The generated answer barely helps answer the question, as it is vague, too detailed, or not detailed enough.
2: The generated answer clearly answers the question.
""",
        "prefix": "Classification",
        "json_output": True,
        "selected_fields": ["Classification", "Reasoning"],
        "label_type": "int",
        "response_template":
        """
Please follow the JSON format below:
```json
{{
  "Reasoning": "Your text here",
  "Classification": "Your integer here"
}}
""",
    },
]

In [ ]:
# 9) Run scenarios and get results

annotation_columns = ['Rater_Oli', 'Rater_chloe', 'Rater_RA']
labels = [0,1,2]

# Filter labeled data (drop rows with NaN in any annotation column)
labeled_data = data.dropna(subset=annotation_columns)
unlabeled_data = data[~data.index.isin(labeled_data.index)]

n_runs = 3  # Number of runs per scenario
verbose = True  # Whether to print verbose output

# Run the scenarios - this only runs the LLM and saves all the generated labels
annotated_results_llm = run_scenarios(
    scenarios=scenarios,
    data=labeled_data,
    annotation_columns=annotation_columns,
    labels=labels,
    n_runs=n_runs,
    verbose=verbose
)

Using all labeled data: 72 samples
Scenario 'French' - Train size (all data): 72, No validation set

=== Processing Verbatim 1/72 ===
Prompt:

Vous êtes un assistant chargé d’évaluer des entrées de données.

Les données comprennent les colonnes suivantes :
- "réponse_attendue": Un passage de réponse considérée comme satisfaisante
- "réponse_llm": La réponse fournie par le LLM, à juger
- "iteration": Identifiant

Voici une entrée à évaluer :
réponse_attendue: Le composant reliant les capteurs avec les actionneurs est la carte de controle ou le microcontroleur.

réponse_llm: La partie d'un robot qui relie les capteurs et les moteurs pour aider a eviter les obstacles est generalement appelee le **systeme de controle** ou **unite de controle**. Ce systeme peut inclure un microcontroleur ou un ordinateur embarque qui recoit les donnees des capteurs (comme des capteurs de distance, des cameras, ou des capteurs infrarouges) et utilise ces informations pour prendre des decisions. Ensuite, il e

In [ ]:
# Save the annotated results to a CSV file
annotated_results_llm.to_csv("data/outputs/annotated_results_llm.csv", sep=";", index=False, encoding="utf-8-sig")

In [7]:
# Optionally, load the annotated results from a CSV file if needed

annotated_results_llm = pd.read_csv(
    "data/outputs/annotated_results_llm.csv",
    sep=";",
    encoding="utf-8-sig"
)

In [11]:
# 10) Compute metrics from the detailed results
# First, compute kappa metrics

epsilon = 0.2  # Epsilon parameter for ALT test
annotation_columns = ['Rater_Oli', 'Rater_chloe', 'Rater_RA']
labels = [0,1,2]
verbose = True

kappa_df, detailed_kappa_metrics = compute_kappa_metrics(
    detailed_results_df=annotated_results_llm,
    annotation_columns=annotation_columns,
    labels=labels,
    kappa_weights='linear'
)

print("\n=== Detailed Kappa Metrics ===")
if detailed_kappa_metrics:
    for scenario_key, metrics in detailed_kappa_metrics.items():
        print(f"\nScenario: {scenario_key}")
        
        print("\nLLM vs Human Annotators:")
        print(metrics['llm_vs_human_df'])
        
        print("\nHuman vs Human Annotators:")
        print(metrics['human_vs_human_df'])
else:
    print("No detailed kappa metrics available.")


=== Columns in detailed_results_df (in compute_kappa_metrics) ===
['sample_id', 'split', 'verbatim', 'iteration', 'Rater_Oli', 'Rater_chloe', 'Rater_RA', 'ModelPrediction', 'Reasoning', 'run', 'prompt_name', 'use_validation_set']

=== Detailed Kappa Metrics ===

Scenario: English_iteration_1

LLM vs Human Annotators:
  Human_Annotator  Cohens_Kappa
0       Rater_Oli      0.855228
1     Rater_chloe      0.732248
2        Rater_RA      0.667040

Human vs Human Annotators:
   Annotator_1  Annotator_2  Cohens_Kappa
0    Rater_Oli  Rater_chloe      0.698492
1    Rater_Oli     Rater_RA      0.622166
2  Rater_chloe     Rater_RA      0.722177

Scenario: French_iteration_1

LLM vs Human Annotators:
  Human_Annotator  Cohens_Kappa
0       Rater_Oli      0.810903
1     Rater_chloe      0.798581
2        Rater_RA      0.764449

Human vs Human Annotators:
   Annotator_1  Annotator_2  Cohens_Kappa
0    Rater_Oli  Rater_chloe      0.698492
1    Rater_Oli     Rater_RA      0.622166
2  Rater_chloe    

In [12]:
# Then, run ALT test
alt_test_df = run_alt_test_on_results(
    detailed_results_df=annotated_results_llm,
    annotation_columns=annotation_columns,
    labels=labels,
    epsilon=epsilon,
    alpha=0.05,
    verbose=verbose
)
alt_test_df = alt_test_df.drop(
    columns=["iteration", "run", "use_validation_set", "N_val", "n_runs"]
)

pd.set_option("display.max_colwidth", None)   # show full content in each cell
alt_test_df.tail(2)


=== Columns in detailed_results_df (in run_alt_test_on_results) ===
['sample_id', 'split', 'verbatim', 'iteration', 'Rater_Oli', 'Rater_chloe', 'Rater_RA', 'ModelPrediction', 'Reasoning', 'run', 'prompt_name', 'use_validation_set']
=== ALT Test: Label Debugging ===
Label counts for each rater:
  ModelPrediction: 72 valid labels
  Rater_Oli: 72 valid labels
  Rater_chloe: 72 valid labels
  Rater_RA: 72 valid labels

Label types for each rater:
  ModelPrediction: int64
  Rater_Oli: int64
  Rater_chloe: int64
  Rater_RA: int64

Mixed types across raters: False

=== Converting labels to consistent types ===
Using label_type: int
Model predictions type after conversion: <class 'numpy.int32'>
Rater_Oli type after conversion: <class 'numpy.int32'>
Rater_chloe type after conversion: <class 'numpy.int32'>
Rater_RA type after conversion: <class 'numpy.int32'>
=== Alt-Test: summary ===
P-values for each comparison:
Rater_Oli: p=0.0000 => rejectH0=True | rho_f=0.972, rho_h=0.931
Rater_chloe: p=0.

prompt_name  N_train  winning_rate_train  passed_alt_test_train  \
6     English      216                 1.0                   True   
7      French      216                 1.0                   True   

   avg_adv_prob_train  \
6            0.945988   
7            0.984568   

                                                            p_values_train  
6    [9.868117748596876e-07, 3.972249567916757e-06, 7.586873715637796e-07]  
7  [1.0929319318836524e-10, 1.3408170160937112e-09, 8.111458449124588e-10]

In [13]:
# Finally, compute classification metrics
classification_df = compute_classification_metrics_from_results(
    detailed_results_df=annotated_results_llm,
    annotation_columns=annotation_columns,
    labels=labels
)

pd.set_option("display.max_columns", None)    # show all columns
classification_df


=== Columns in detailed_results_df (in compute_classification_metrics_from_results) ===
['sample_id', 'split', 'verbatim', 'iteration', 'Rater_Oli', 'Rater_chloe', 'Rater_RA', 'ModelPrediction', 'Reasoning', 'run', 'prompt_name', 'use_validation_set']


prompt_name  iteration  n_runs  use_validation_set  N_train  N_val  \
0     English          1       3               False      216      0   
1      French          1       3               False      216      0   

   global_accuracy_train  global_recall_train  global_error_rate_train  \
0               0.847222             0.841629                 0.152778   
1               0.884259             0.857848                 0.115741   

   class_0_recall_train  class_0_error_rate_train  \
0              0.666667                  0.333333   
1              0.853333                  0.146667   

   class_0_correct_count_train  class_0_missed_count_train  \
0                           50                          25   
1                           64                          11   

   class_0_false_positives_train  class_1_recall_train  \
0                              0              0.897436   
1                              4              0.769231   

   class_1_error_rate_train  class_1_correct_count_train  \
0                  0.102564                           35   
1                  0.230769                           30   

   class_1_missed_count_train  class_1_false_positives_train  \
0                           4                             29   
1                           9                             14   

   class_2_recall_train  class_2_error_rate_train  \
0              0.960784                  0.039216   
1              0.950980                  0.049020   

   class_2_correct_count_train  class_2_missed_count_train  \
0                           98                           4   
1                           97                           5   

   class_2_false_positives_train  
0                              4  
1                              7

In [ ]:
verbose = True
labels = [0,1,2]
annotation_columns = []
epsilon = 0.2
n_runs = 1  

scenarios = [
    {
        "provider_llm1": "azure",
        "model_name_llm1": "gpt-4o",
        "temperature_llm1": 0,

        # For the "improver" LLM2
        "provider_llm2": "azure",
        "model_name_llm2": "gpt-4o",
        "temperature_llm2": 0.7,

        "max_iterations": 1,
        "n_completions": 1,
        "prompt_name": "French",
        
        # Data configuration
        "subsample_size": -1,  # Size of data subset to use
        "use_validation_set": False,  # Whether to use a validation set
        "validation_size": 10,  # Size of validation set (if used)
        "random_state": 42,  # Random state for reproducibility

        # Our initial prompt
        "template": """
Vous êtes un assistant chargé d’évaluer des entrées de données.

Les données comprennent les colonnes suivantes :
- "réponse_attendue": Un passage de réponse considérée comme satisfaisante
- "réponse_llm": La réponse fournie par le LLM, à juger
- "iteration": Identifiant

Voici une entrée à évaluer :
{verbatim_text}

Tâche d’évaluation :
Évaluer si la réponse_llm répond adéquatement, c'est à dire qu'elle correspond à la réponse attendue, en utilisant l’échelle suivante :

0 : La réponse générée ne permet pas du tout de répondre à la question posée (hors sujet, incomplète ou incorrecte).
1 : La réponse générée permet difficilement de répondre à la question, car elle est vague, trop ou pas assez détaillée.
2 : La réponse générée permet de répondre clairement à la question.
""",
        "prefix": "Classification",
        "json_output": True,
        "selected_fields": ["Classification", "Reasoning"],
        "label_type": "int",
        "response_template":
        """
Please follow the JSON format below:
```json
{{
  "Reasoning": "Your text here",
  "Classification": "Your integer here"
}}
""",
    },
]

# Run the scenarios - this only runs the LLM and saves all the generated labels
full_results_llm = run_scenarios(
    scenarios=scenarios,
    data=data,
    annotation_columns=annotation_columns,
    labels=labels,
    n_runs=n_runs,
    verbose=verbose
)

Using all labeled data: 720 samples
Scenario 'French' - Train size (all data): 720, No validation set

=== Processing Verbatim 1/720 ===
Prompt:

Vous êtes un assistant chargé d’évaluer des entrées de données.

Les données comprennent les colonnes suivantes :
- "réponse_attendue": Un passage de réponse considérée comme satisfaisante
- "réponse_llm": La réponse fournie par le LLM, à juger
- "iteration": Identifiant

Voici une entrée à évaluer :
réponse_attendue: Le composant reliant les capteurs avec les actionneurs est la carte de controle ou le microcontroleur.

réponse_llm: La partie d'un robot qui relie les capteurs et les moteurs pour aider a eviter les obstacles est generalement appelee le **systeme de controle** ou **unite de controle**. Ce systeme peut inclure un microcontroleur ou un ordinateur embarque qui recoit les donnees des capteurs (comme des capteurs de distance, des cameras, ou des capteurs infrarouges) et utilise ces informations pour prendre des decisions. Ensuite, i

In [ ]:
# turn the index of `data` into a column that matches full_results_llm
data_pos = (
    data
      .reset_index()                      # old index → new column "index"
      .rename(columns={"index": "sample_id"})
)

# keep only the columns you actually want from the LLM results
llm_subset = full_results_llm[["sample_id", "ModelPrediction", "Reasoning"]]

# one-to-one merge; pandas will raise if the assumption is broken
full_merged_results_llm = data_pos.merge(
            llm_subset,
            on="sample_id",
            how="left",
            validate="one_to_one"         # guarantees no duplicates creep in
         )

# put sample_id back as the index so the shape matches the original
full_merged_results_llm = full_merged_results_llm.set_index("sample_id")

In [19]:
full_merged_results_llm.to_csv("data/outputs/full_results_llm.csv", sep=";", index=False, encoding="utf-8-sig")